# Sujet 3 : L'épidémie de choléra à Londres en 1854

Nous chargeons deux bibliothèques spécifiques au traitement des données spatiales :

* [folium](https://python-visualization.github.io/folium/index.html), qui permet d'afficher des cartes avec python et Leaflet.js ;
* [geopandas](https://geopandas.org/) qui permet de prendre en compte la nature géographique des données traitées. 

In [1]:
import folium
import pyproj
import geopandas as gpd

## Importation et prétrtaitements des données

Nous lisons les fichiers géographiques (format Shape d'ESRI), et les convertissions en *dataframes* de la bibliothèque geopandas.

### Cas de choléras

In [2]:
cholera_deaths = gpd.read_file('Cholera_Deaths.shp',encoding='ANSI') 

In [3]:
cholera_deaths.crs

{'proj': 'tmerc',
 'lat_0': 49,
 'lon_0': -2,
 'k': 0.9996012717,
 'x_0': 400000,
 'y_0': -100000,
 'ellps': 'airy',
 'units': 'm',
 'no_defs': True}

Nous reprojetons ces couches géographiques dans un référentiel géographique (défini par le code EPSG) exploitable sous folium. Attention, la valeur de l'attribut 'crs' écrit sous la forme "EPSG:4326" ne fonctionnera pas sous Windows (version pyproj 3.0.0.post1) :

* ligne 359-360 de la fonction \_\_init\_\_.py : *# EPSG only works on case-insensitive filesystems* 
* nous utilisons donc l'autre manière d'écrire cet argument (https://geopandas.org/projections.html), en minuscule

Les deux écritures sont cependant possible sous Linux : cf. version pyproj, et ce que dit le fichier \_\_init\_\_.py ?

In [4]:
cholera_deaths = cholera_deaths.to_crs(epsg = 4326)

Comme nous avons beaucoup de cas à cartographier, nous convertissons notre geopandas *dataframe* en un fichier **geojson**, un format de données géographiques courant, directement lisible par folium.

In [5]:
cholera_deaths.to_file("cholera_deaths.geojson", driver='GeoJSON')

Nous initialisons la carte produite par **folium**, en la centrant sur un point et en définissant un niveau de zoom.

In [6]:
### Initialisation de la carte, et ajout direct des cas de cholera

In [7]:
carte_snow_1854 = folium.Map(location = [51.514 , -0.1365], zoom_start=17)

In [8]:
folium.GeoJson("cholera_deaths.geojson", name="Incidences").add_to(carte_snow_1854)

### Pompes à eau

In [9]:
pumps = gpd.read_file('Pumps.shp')

In [10]:
pumps = pumps.to_crs(epsg = 4326)

In [11]:
pumps.to_file("pumps.geojson", driver = 'GeoJSON')

In [13]:
[folium.CircleMarker([pumps.geometry.y[i], pumps.geometry.x[i]] , popup = "Pompes", color = 'red', radius = 100).add_to(carte_snow_1854) for i in range(len(pumps.geometry.x))]

La méthode *LayerControl* permet de gérer l'affichage de plusieurs couches géographiques

In [14]:
folium.LayerControl().add_to(carte_snow_1854)

## Affichage de la carte

In [15]:
carte_snow_1854